In [2]:
%matplotlib inline
%matplotlib nbagg
import pickle
import tensorflow as tf
import numpy as np
import matplotlib.pyplot as plt
import prettytensor as pt

In [3]:
rows, cols = 70, 100
img_shape = (rows, cols)
img_flat_size = rows * cols
img_classes = 2
img_channels = 3

phase = pt.Phase.train

In [4]:
resized_folder_path = "/home/openroot/Tanmoy/Working Stuffs/myStuffs/havss-tf/ISIC-2017/resized/"

In [5]:
isic_pickle_file = resized_folder_path + "ISIC.pickle"
with open(isic_pickle_file, "rb") as f:
    save = pickle.load(f)
    train_dataset =  save["train_dataset"]
    train_labels =  save["train_labels"]
    validation_dataset =  save["validation_dataset"]
    validation_labels =  save["validation_labels"]
    test_dataset =  save["test_dataset"]
    test_labels =  save["test_labels"]
    del save
    print("Training Set {0} {1}".format(train_dataset.shape, train_labels.shape))
    print("Validation Set {0} {1}".format(validation_dataset.shape, validation_labels.shape))    
    print("Test Set {0} {1}".format(test_dataset.shape, test_labels.shape))
print test_labels[0:10, :]
test_dataset_info = np.sum(test_labels[:, :], axis = 0)
print("Test Dataset Info : [1, 0] = {0}, [0, 1] = {1}".format(test_dataset_info[0], test_dataset_info[1]))
train_dataset_info = np.sum(validation_labels[:, :], axis = 0)
print("Validation Dataset Info : [1, 0] = {0}, [0, 1] = {1}".format(train_dataset_info[0], train_dataset_info[1]))
train_dataset_info = np.sum(train_labels[:, :], axis = 0)
print("Train Dataset Info : [1, 0] = {0}, [0, 1] = {1}".format(train_dataset_info[0], train_dataset_info[1]))

Training Set (37904, 70, 100, 3) (37904, 2)
Validation Set (6152, 70, 100, 3) (6152, 2)
Test Set (6152, 70, 100, 3) (6152, 2)
[[ 0.  1.]
 [ 0.  1.]
 [ 1.  0.]
 [ 1.  0.]
 [ 1.  0.]
 [ 1.  0.]
 [ 0.  1.]
 [ 1.  0.]
 [ 1.  0.]
 [ 0.  1.]]
Test Dataset Info : [1, 0] = 2786.0, [0, 1] = 3366.0
Validation Dataset Info : [1, 0] = 2522.0, [0, 1] = 3630.0
Train Dataset Info : [1, 0] = 20612.0, [0, 1] = 17292.0


In [6]:
# input_x = tf.placeholder(tf.float32, [None, img_flat_size], name = "input_x") 
input_layer = tf.placeholder(tf.float32, [None, rows, cols, img_channels], name = "input_layer")
y_true = tf.placeholder(tf.float32, [None, img_classes], name = "y_true")
y_true_cls = tf.argmax(y_true, dimension = 1)

In [7]:
x_pretty = pt.wrap(input_layer)
with pt.defaults_scope(activation_fn = tf.nn.relu):
    y_pred, loss = x_pretty.\
        conv2d(kernel = 5, depth = 16, name = "conv_layer_1").\
        max_pool(kernel = 2, stride = 2).\
        dropout(keep_prob=0.8, phase=phase).\
        conv2d(kernel = 5, depth = 32, name = "conv_layer_2").\
        max_pool(kernel = 2, stride = 2).\
        dropout(keep_prob=0.8, phase=phase).\
        conv2d(kernel = 5, depth = 64, name = "conv_layer_3").\
        max_pool(kernel = 2, stride = 2).\
        flatten().\
        fully_connected(size = 256, name = "fc_layer_2", activation_fn = tf.nn.relu).\
        softmax_classifier(num_classes = img_classes, labels = y_true)

In [8]:
global_step = tf.Variable(0, trainable=False)
learning_rate = tf.train.exponential_decay(0.1, global_step, train_labels.shape[0], 0.95, staircase=True)

In [9]:
optimizer = tf.train.AdamOptimizer(learning_rate = 0.001).minimize(loss)

In [10]:
y_pred_cls = tf.argmax(y_pred, dimension = 1)

In [11]:
correct_pred = tf.equal(y_true_cls, y_pred_cls)

In [12]:
accuracy = tf.reduce_mean(tf.cast(correct_pred, tf.float32))

In [13]:
train_batch_size = 5
prev_train_acc = 0
prev_train_acc_step = 0
min_train_acc_step = 1000
offset = 0

In [14]:
# num_steps = 12000
# with tf.Session() as sess:
#     tf.global_variables_initializer().run()
#     print("Variable Initialized")
#     for step in range(num_steps):
#         offset = (step * train_batch_size) % (train_labels.shape[0] - train_batch_size)
# #         print offset
#         batch_train = train_dataset[offset:(offset + train_batch_size), :, : ,:]
#         batch_labels = train_labels[offset:(offset + train_batch_size), :]
#         feed_dict_train = {
#             input_layer: batch_train,
#             y_true: batch_labels
#         }
        
#         _, l = sess.run([optimizer, loss], feed_dict = feed_dict_train)
#         print("Step : {0} - Loss : {1}".format(step, l))
        

#         if step % 200 :
#             feed_dict_valid = {
#                 input_layer: validation_dataset,
#                 y_true: validation_labels
#             }

#             valid_acc = sess.run([accuracy], feed_dict = feed_dict_valid)
#             print("Step : {0} - Validation Accuracy : {1} ".format(step, train_loss))
            
#     phase = pt.Phase.test    
#     feed_dict_test = {
#         input_layer: test_dataset,
#         y_true: test_labels
#     }
#     true_value_class, acc, pred_value, pred_value_class = sess.run([y_true_cls, accuracy, y_pred, y_pred_cls], feed_dict = feed_dict_test)
#     print("Accuracy {:.2%}".format(acc))
#     print("True Value Class")
#     print true_value_class[0:10]
#     print("Pred Value")
#     print pred_value[0:20]
#     print("Pred Value Class")
#     print pred_value_class

In [15]:
def runModel(epoch):
    with tf.Session() as sess:
        tf.global_variables_initializer().run()
        print("Variables Initialized")
        total_data_len = train_labels.shape[0]
        print total_data_len
        num_step = int(total_data_len / train_batch_size)
        print("Batch Size : {0}".format(train_batch_size))
        print("Starting Training")
        for i in range(epoch):
            print("Epoch - {0} ".format(i))
            for step in range(num_step):
                offset = (step * train_batch_size) % (total_data_len - train_batch_size)
#                 print offset
                batch_train = train_dataset[offset:(offset + train_batch_size), :, :, :]
                batch_labels = train_labels[offset:(offset + train_batch_size), :]
                feed_dict_train = {
                    input_layer: batch_train,
                    y_true: batch_labels
#                     global_step: step * train_batch_size
                }

                _, train_loss = sess.run([optimizer, loss], feed_dict = feed_dict_train)
                print("Step : {0} - Training Loss : {1}".format(step, train_loss))
                
#                 if step % 200 :
#                     feed_dict_valid = {
#                         input_layer: validation_dataset,
#                         y_true: validation_labels
#                     }
                    
#                     valid_acc = sess.run([accuracy], feed_dict = feed_dict_valid)
#                     print("Step : {0} - Validation Accuracy : {1} ".format(step, train_loss))
                    
#                     if valid_acc > prev_train_acc:
#                         print("Imporvement Found : {0}, Step Difference : {1}".format(valid_acc - prev_train_acc, step - prev_train_acc_step))
#                         prev_train_acc_step = step
#                         prev_train_acc = valid_acc
#                     else:
#                         if prev_train_acc_step - step > min_train_acc_step:
#                             print("No Improvement Found : Step Difference : {0}".format(step - prev_train_acc_step))
#                             print("Therefore Ending Training")
#                             break
        print("Training Completed!!!")
        print("Staring Testing Phase")
        phase = pt.Phase.test    
        feed_dict_test = {
            input_layer: test_dataset,
            y_true: test_labels
        }      
        test_acc = sess.run([accuracy], feed_dict = feed_dict_test)
        print("Testing Accuracy : {0}".format(test_acc))

In [ ]:
runModel(10)

Variables Initialized
37904
Batch Size : 5
Starting Training
Epoch - 0 
Step : 0 - Training Loss : 21.4575386047
Step : 1 - Training Loss : 29.6497535706
Step : 2 - Training Loss : 0.000199957023142
Step : 3 - Training Loss : 5.56584644318
Step : 4 - Training Loss : 32.7967758179
Step : 5 - Training Loss : 6.30236053467
Step : 6 - Training Loss : 7.73404312134
Step : 7 - Training Loss : 1.95678305626
Step : 8 - Training Loss : 4.8915438652
Step : 9 - Training Loss : 8.86676120758
Step : 10 - Training Loss : 0.517079770565
Step : 11 - Training Loss : 0.270165354013
Step : 12 - Training Loss : 11.4172840118
Step : 13 - Training Loss : 6.30052185059
Step : 14 - Training Loss : 2.76858592033
Step : 15 - Training Loss : 0.268348276615
Step : 16 - Training Loss : 1.54748368263
Step : 17 - Training Loss : 0.581346154213
Step : 18 - Training Loss : 4.97078561783
Step : 19 - Training Loss : 1.30211997032
Step : 20 - Training Loss : 7.70099544525
Step : 21 - Training Loss : 1.5318915844
Step : 2

Step : 190 - Training Loss : 1.35182976723
Step : 191 - Training Loss : 0.657889962196
Step : 192 - Training Loss : 0.609384000301
Step : 193 - Training Loss : 0.961142063141
Step : 194 - Training Loss : 0.579736828804
Step : 195 - Training Loss : 0.241577237844
Step : 196 - Training Loss : 0.33291849494
Step : 197 - Training Loss : 2.5447742939
Step : 198 - Training Loss : 1.16533231735
Step : 199 - Training Loss : 0.899353861809
Step : 200 - Training Loss : 1.32498955727
Step : 201 - Training Loss : 0.129071518779
Step : 202 - Training Loss : 1.11147320271
Step : 203 - Training Loss : 0.805870652199
Step : 204 - Training Loss : 1.42568016052
Step : 205 - Training Loss : 0.658090233803
Step : 206 - Training Loss : 0.688913524151
Step : 207 - Training Loss : 1.70473504066
Step : 208 - Training Loss : 1.00779235363
Step : 209 - Training Loss : 0.808412373066
Step : 210 - Training Loss : 0.458694547415
Step : 211 - Training Loss : 546.207702637
Step : 212 - Training Loss : 0.668356060982

Step : 378 - Training Loss : 0.421681314707
Step : 379 - Training Loss : 0.735747694969
Step : 380 - Training Loss : 0.701469779015
Step : 381 - Training Loss : 0.678258061409
Step : 382 - Training Loss : 0.582709729671
Step : 383 - Training Loss : 1.66191899776
Step : 384 - Training Loss : 0.687224805355
Step : 385 - Training Loss : 0.658891022205
Step : 386 - Training Loss : 0.559978842735
Step : 387 - Training Loss : 0.570264577866
Step : 388 - Training Loss : 0.71626162529
Step : 389 - Training Loss : 0.676994144917
Step : 390 - Training Loss : 0.711091637611
Step : 391 - Training Loss : 0.69306820631
Step : 392 - Training Loss : 0.656246423721
Step : 393 - Training Loss : 0.66025185585
Step : 394 - Training Loss : 0.674185037613
Step : 395 - Training Loss : 0.644011497498
Step : 396 - Training Loss : 0.699646174908
Step : 397 - Training Loss : 0.694307804108
Step : 398 - Training Loss : 0.671954214573
Step : 399 - Training Loss : 0.6804946661
Step : 400 - Training Loss : 0.7063272

Step : 566 - Training Loss : 0.634237766266
Step : 567 - Training Loss : 0.572465658188
Step : 568 - Training Loss : 0.729291498661
Step : 569 - Training Loss : 0.534638881683
Step : 570 - Training Loss : 0.668170452118
Step : 571 - Training Loss : 0.694200873375
Step : 572 - Training Loss : 0.663195252419
Step : 573 - Training Loss : 0.681937515736
Step : 574 - Training Loss : 3.31228590012
Step : 575 - Training Loss : 0.647989392281
Step : 576 - Training Loss : 0.619992136955
Step : 577 - Training Loss : 0.755659103394
Step : 578 - Training Loss : 0.591221690178
Step : 579 - Training Loss : 0.643996715546
Step : 580 - Training Loss : 0.675706744194
Step : 581 - Training Loss : 0.687476634979
Step : 582 - Training Loss : 0.505931019783
Step : 583 - Training Loss : 0.662322878838
Step : 584 - Training Loss : 1.30634939671
Step : 585 - Training Loss : 0.786025643349
Step : 586 - Training Loss : 0.769238948822
Step : 587 - Training Loss : 0.768793344498
Step : 588 - Training Loss : 0.802

Step : 753 - Training Loss : 0.6656229496
Step : 754 - Training Loss : 0.801259815693
Step : 755 - Training Loss : 0.725773692131
Step : 756 - Training Loss : 0.617682397366
Step : 757 - Training Loss : 0.569130778313
Step : 758 - Training Loss : 0.690943598747
Step : 759 - Training Loss : 0.661140561104
Step : 760 - Training Loss : 0.650551974773
Step : 761 - Training Loss : 0.693230986595
Step : 762 - Training Loss : 0.548007428646
Step : 763 - Training Loss : 0.717288374901
Step : 764 - Training Loss : 0.67655479908
Step : 765 - Training Loss : 0.776829838753
Step : 766 - Training Loss : 0.649852573872
Step : 767 - Training Loss : 0.681454479694
Step : 768 - Training Loss : 0.704672157764
Step : 769 - Training Loss : 0.546464502811
Step : 770 - Training Loss : 0.626327157021
Step : 771 - Training Loss : 0.709233403206
Step : 772 - Training Loss : 0.67221224308
Step : 773 - Training Loss : 0.685841739178
Step : 774 - Training Loss : 0.660362362862
Step : 775 - Training Loss : 0.62656

...

Step : 6802 - Training Loss : 0.049229092896
Step : 6803 - Training Loss : 5.46381452295e-05
Step : 6804 - Training Loss : 0.00466779666021
Step : 6805 - Training Loss : 0.15982618928
Step : 6806 - Training Loss : 0.00435840850696
Step : 6807 - Training Loss : 0.100849285722
Step : 6808 - Training Loss : 2.21955378947e-05
Step : 6809 - Training Loss : 0.010676654987
Step : 6810 - Training Loss : 0.15939296782
Step : 6811 - Training Loss : 1.78813138518e-06
Step : 6812 - Training Loss : 3.71984481812
Step : 6813 - Training Loss : 7.15255623618e-08
Step : 6814 - Training Loss : 0.048342205584
Step : 6815 - Training Loss : 1.07288099116e-06
Step : 6816 - Training Loss : 0.000151505329995
Step : 6817 - Training Loss : 0.01236451976
Step : 6818 - Training Loss : 0.0775134786963
Step : 6819 - Training Loss : 1.07288110485e-06
Step : 6820 - Training Loss : 0.15914657712
Step : 6821 - Training Loss : 7.19461822882e-05
Step : 6822 - Training Loss : 0.47726097703
Step : 6823 - Training Loss : 0.

Step : 6980 - Training Loss : 0.000333342730301
Step : 6981 - Training Loss : 3.11835392495e-05
Step : 6982 - Training Loss : 0.0106479777023
Step : 6983 - Training Loss : 0.157481402159
Step : 6984 - Training Loss : 3.0994391409e-07
Step : 6985 - Training Loss : 0.00137019902468
Step : 6986 - Training Loss : 1.50203322846e-06
Step : 6987 - Training Loss : 2.62260300588e-07
Step : 6988 - Training Loss : 7.14889683877e-05
Step : 6989 - Training Loss : 0.000926194421481
Step : 6990 - Training Loss : 6.67571271151e-07
Step : 6991 - Training Loss : 0.00030571577372
Step : 6992 - Training Loss : 0.00127823266666
Step : 6993 - Training Loss : 0.000368407927454
Step : 6994 - Training Loss : 0.000203623945708
Step : 6995 - Training Loss : 0.000176381247002
Step : 6996 - Training Loss : 0.000947976368479
Step : 6997 - Training Loss : 0.00163490721025
Step : 6998 - Training Loss : 0.00059442530619
Step : 6999 - Training Loss : 7.15255694672e-08
Step : 7000 - Training Loss : 0.00397397298366
Step

Step : 7158 - Training Loss : 3.95269235014e-05
Step : 7159 - Training Loss : 0.121496245265
Step : 7160 - Training Loss : 0.0510762035847
Step : 7161 - Training Loss : 1.34227420858e-05
Step : 7162 - Training Loss : 0.204570382833
Step : 7163 - Training Loss : 0.0941069349647
Step : 7164 - Training Loss : 0.0485378466547
Step : 7165 - Training Loss : 0.0
Step : 7166 - Training Loss : 2.5272286166e-06
Step : 7167 - Training Loss : 0.0910393819213
Step : 7168 - Training Loss : 0.121331050992
Step : 7169 - Training Loss : 1.78049147129
Step : 7170 - Training Loss : 0.159361883998
Step : 7171 - Training Loss : 2.00261747523e-05
Step : 7172 - Training Loss : 3.83851738661e-06
Step : 7173 - Training Loss : 0.157889455557
Step : 7174 - Training Loss : 0.0242466721684
Step : 7175 - Training Loss : 0.157972544432
Step : 7176 - Training Loss : 0.000192489576875
Step : 7177 - Training Loss : 5.01569811604e-05
Step : 7178 - Training Loss : 9.98952691589e-06
Step : 7179 - Training Loss : 0.0013224

Step : 7338 - Training Loss : 6.66745909257e-05
Step : 7339 - Training Loss : 0.0814414173365
Step : 7340 - Training Loss : 0.00196670740843
Step : 7341 - Training Loss : 0.135733753443
Step : 7342 - Training Loss : 0.119942367077
Step : 7343 - Training Loss : 0.342846363783
Step : 7344 - Training Loss : 0.159339040518
Step : 7345 - Training Loss : 0.163421630859
Step : 7346 - Training Loss : 0.159414842725
Step : 7347 - Training Loss : 1.76898756763e-05
Step : 7348 - Training Loss : 0.1198874861
Step : 7349 - Training Loss : 2.16954995267e-05
Step : 7350 - Training Loss : 0.000159010945936
Step : 7351 - Training Loss : 0.119746997952
Step : 7352 - Training Loss : 4.76837129781e-08
Step : 7353 - Training Loss : 0.0
Step : 7354 - Training Loss : 0.343250930309
Step : 7355 - Training Loss : 0.130529090762
Step : 7356 - Training Loss : 0.0415203198791
Step : 7357 - Training Loss : 2.38418564891e-08
Step : 7358 - Training Loss : 2.38418564891e-08
Step : 7359 - Training Loss : 0.05422212556

Step : 7518 - Training Loss : 0.00168239022605
Step : 7519 - Training Loss : 6.63648825139e-05
Step : 7520 - Training Loss : 0.0366312265396
Step : 7521 - Training Loss : 0.0
Step : 7522 - Training Loss : 4.76837094254e-08
Step : 7523 - Training Loss : 0.0520168915391
Step : 7524 - Training Loss : 5.64972579014e-05
Step : 7525 - Training Loss : 0.11954305321
Step : 7526 - Training Loss : 0.0674730986357
Step : 7527 - Training Loss : 0.0716597139835
Step : 7528 - Training Loss : 0.646414458752
Step : 7529 - Training Loss : 0.000193442130694
Step : 7530 - Training Loss : 0.343364745378
Step : 7531 - Training Loss : 1.52346347022e-05
Step : 7532 - Training Loss : 2.44364109676e-05
Step : 7533 - Training Loss : 1.28745830352e-06
Step : 7534 - Training Loss : 0.16011698544
Step : 7535 - Training Loss : 0.0135156111792
Step : 7536 - Training Loss : 5.96045538259e-07
Step : 7537 - Training Loss : 0.0526343211532
Step : 7538 - Training Loss : 0.731670260429
Step : 7539 - Training Loss : 1.8500